In [1]:
import torch
import torch.nn as nn
import torch.nn.functional as F
import math
from einops import rearrange

# Patch Embedding with Dynamic Positional Encoding
class DynamicPatchEmbedding(nn.Module):
    def __init__(self, in_channels=3, patch_size=8, emb_dim=768, img_size=256):
        super(DynamicPatchEmbedding, self).__init__()
        self.patch_size = patch_size
        self.proj = nn.Conv2d(in_channels, emb_dim, kernel_size=patch_size, stride=patch_size)
        self.num_patches = (img_size // patch_size) ** 2

    def forward(self, x):
        # Reshape the input to 4D if necessary
        if len(x.shape) == 2:
            batch_size = x.shape[0]
            channels = 3  # Assuming 3 feature channels
            h = w = int(math.sqrt(x.shape[1] // channels))  # Infer height and width
            x = x.view(batch_size, channels, h, w)  # Reshape to [batch_size, channels, height, width]
        
        x = self.proj(x)  # Apply Conv2d
        x = x.flatten(2).transpose(1, 2)  # (batch_size, num_patches, emb_dim)
        return x
    
# Style Adaptive Layer Normalization (SALN)
class StyleAdaptiveLayerNorm(nn.Module):
    def __init__(self, emb_dim):
        super(StyleAdaptiveLayerNorm, self).__init__()
        self.norm = nn.LayerNorm(emb_dim)
        self.fc = nn.Linear(emb_dim, emb_dim * 2)

    def forward(self, x, style):
        style = self.fc(style).unsqueeze(1)
        gamma, beta = style.chunk(2, dim=-1)
        normalized_x = self.norm(x)
        return gamma * normalized_x + beta

# LayerNorm-based Attention Conditioning using Pre-learned Attention Weights
class AttentionConditioning(nn.Module):
    def __init__(self, emb_dim, learned_attn_weights):
        super(AttentionConditioning, self).__init__()
        self.learned_attn_weights = learned_attn_weights
        self.norm = nn.LayerNorm(emb_dim)

    def forward(self, untrained_attn_weights):
        # Condition untrained weights using pre-learned attention weights
        conditioned_weights = self.learned_attn_weights + untrained_attn_weights
        return self.norm(conditioned_weights)

# Cross-Attention Layer
class CrossAttentionLayer(nn.Module):
    def __init__(self, emb_dim, num_heads, dropout=0.1):
        super(CrossAttentionLayer, self).__init__()
        self.attn = nn.MultiheadAttention(embed_dim=emb_dim, num_heads=num_heads, batch_first=True)
        self.dropout = nn.Dropout(dropout)

    def forward(self, x, context):
        attn_output, _ = self.attn(x, context, context)
        return self.dropout(attn_output)

# Transformer Encoder Block with Pre-learned Attention Conditioning
class TransformerEncoderBlock(nn.Module):
    def __init__(self, emb_dim=768, num_heads=8, hidden_dim=3, learned_attn_weights=None, dropout=0.1):
        super(TransformerEncoderBlock, self).__init__()
        self.attn = CrossAttentionLayer(emb_dim, num_heads, dropout)
        self.ff = nn.Sequential(
            nn.Linear(emb_dim, hidden_dim),
            nn.ReLU(),
            nn.Linear(hidden_dim, emb_dim),
        )
        self.norm1 = AttentionConditioning(emb_dim, learned_attn_weights) if learned_attn_weights is not None else nn.LayerNorm(emb_dim)
        self.norm2 = StyleAdaptiveLayerNorm(emb_dim)
        self.dropout = nn.Dropout(dropout)

    def forward(self, x, style):
        attn_output = self.attn(x, x)
        x = x + self.dropout(attn_output)
        x = self.norm1(x)

        ff_output = self.ff(x)
        x = x + self.dropout(ff_output)
        x = self.norm2(x)
        return x

# Transformer Decoder Block
class TransformerDecoderBlock(nn.Module):
    def __init__(self, emb_dim=768, num_heads=8, hidden_dim=3, dropout=0.1):
        super(TransformerDecoderBlock, self).__init__()
        self.attn1 = CrossAttentionLayer(emb_dim, num_heads, dropout)
        self.attn2 = CrossAttentionLayer(emb_dim, num_heads, dropout)
        self.ff = nn.Sequential(
            nn.Linear(emb_dim, hidden_dim),
            nn.ReLU(),
            nn.Linear(hidden_dim, emb_dim),
        )
        self.norm1 = StyleAdaptiveLayerNorm(emb_dim)
        self.norm2 = StyleAdaptiveLayerNorm(emb_dim)
        self.norm3 = StyleAdaptiveLayerNorm(emb_dim)

    def forward(self, x, enc_output, style):
        attn_output1 = self.attn1(x, x)
        x = x + attn_output1
        x = self.norm1(x)

        attn_output2 = self.attn2(x, enc_output)
        x = x + attn_output2
        x = self.norm2(x)

        ff_output = self.ff(x)
        x = x + ff_output
        x = self.norm3(x)

        return x

# Swin Transformer Block
class SwinTransformerBlock(nn.Module):
    def __init__(self, dim, num_heads, window_size=7, shift_size=2):
        super(SwinTransformerBlock, self).__init__()
        self.attn = nn.MultiheadAttention(embed_dim=dim, num_heads=num_heads, batch_first=True)
        self.mlp = nn.Sequential(
            nn.Linear(dim, 4 * dim),
            nn.GELU(),
            nn.Linear(4 * dim, dim)
        )
        self.norm1 = nn.LayerNorm(dim)
        self.norm2 = nn.LayerNorm(dim)

    def forward(self, x):
        shortcut = x
        x = self.norm1(x)
        x, _ = self.attn(x, x, x)
        x = shortcut + x

        shortcut = x
        x = self.norm2(x)
        x = self.mlp(x)
        x = shortcut + x

        return x

# Refinement Block
class RefinementBlock(nn.Module):
    def __init__(self, in_channels=768, out_channels=3, kernel_size=3, stride=1, padding=1):
        super(RefinementBlock, self).__init__()
        self.conv = nn.Conv2d(in_channels, out_channels, kernel_size, stride, padding)
        self.bn = nn.BatchNorm2d(out_channels)
        self.relu = nn.ReLU(inplace=True)

    def forward(self, x):
        x = self.conv(x)
        x = self.bn(x)
        x = self.relu(x)
        return x

class MultiScaleStyleEncoder(nn.Module):
    def __init__(self, emb_dim):
        super().__init__()
        self.conv = nn.Conv2d(3, emb_dim, kernel_size=3, stride=2, padding=1)
        self.pool1 = nn.AdaptiveAvgPool2d(16)
        self.pool2 = nn.AdaptiveAvgPool2d(8)
        self.pool3 = nn.AdaptiveAvgPool2d(4)
        self.fc = nn.Linear(emb_dim * (16*16 + 8*8 + 4*4), emb_dim)

    def forward(self, x):
        x = F.relu(self.conv(x))
        x1 = self.pool1(x).flatten(1)
        x2 = self.pool2(x).flatten(1)
        x3 = self.pool3(x).flatten(1)
        x = torch.cat([x1, x2, x3], dim=1)
        return self.fc(x)

# Main RealFormer v3 with AGA Attention Conditioning
class RealFormerAGA(nn.Module):
    def __init__(self, img_size=512, patch_size=8, emb_dim=768, num_heads=12, num_layers=12, hidden_dim=3072, window_size=8, learned_attn_weights=None):
        super(RealFormerAGA, self).__init__()
        self.patch_embed = DynamicPatchEmbedding(in_channels=3, patch_size=patch_size, emb_dim=emb_dim, img_size=img_size)

        # Encoder with pre-learned attention conditioning
        self.encoder_layers = nn.ModuleList([TransformerEncoderBlock(emb_dim, num_heads, hidden_dim, learned_attn_weights) for _ in range(num_layers)])
        self.decoder_layers = nn.ModuleList([TransformerDecoderBlock(emb_dim, num_heads, hidden_dim) for _ in range(num_layers)])
        self.swin_layers = nn.ModuleList([SwinTransformerBlock(emb_dim, num_heads, window_size) for _ in range(num_layers)])

        self.refinement = RefinementBlock(in_channels=emb_dim, out_channels=3)
        self.final_layer = nn.Conv2d(3, 3, kernel_size=1)  # Adjust the input channels to 3

        # Style encoder
        self.style_encoder = MultiScaleStyleEncoder(emb_dim)

    def forward(self, frame_t, frame_t1, learned_attn_weights):
        # Patch embedding for consecutive frames
        x_t = self.patch_embed(frame_t)
        x_t1 = self.patch_embed(frame_t1)

        # Style encoding from previous frames
        style_features = self.style_encoder(frame_t1)

        # Conditioning learned attention weights prior to untrained attention
        for encoder in self.encoder_layers:
            x_t = encoder(x_t, style_features)

        # Transformer decoder to reconstruct the next frame
        for decoder in self.decoder_layers:
            x_t1 = decoder(x_t1, x_t, style_features)

        # Swin Transformer processing for temporal coherence
        for swin in self.swin_layers:
            x_t1 = swin(x_t1)

        # Final refinement and output
        batch_size, num_patches, emb_dim = x_t1.shape
        h = w = int(math.sqrt(num_patches))  # Assuming square patches
        x_t1 = x_t1.transpose(1, 2).view(batch_size, emb_dim, h, w)
        
        x_t1 = self.refinement(x_t1)
        x_t1 = self.final_layer(x_t1)
        return x_t1

# Loss functions remain the same
def total_variation_loss(x):
    return torch.sum(torch.abs(x[:, :, :-1, :] - x[:, :, 1:, :])) + torch.sum(torch.abs(x[:, :, :, :-1] - x[:, :, :, 1:]))

def combined_loss(output, target):
    l1_loss = nn.L1Loss()(output, target)
    tv_loss = total_variation_loss(output)
    return l1_loss + 0.0001 * tv_loss

def psnr(img1, img2):
    mse = torch.mean((img1 - img2) ** 2)
    if mse == 0:
        return float('inf')
    return 20 * torch.log10(1.0 / torch.sqrt(mse))

In [154]:
from torch.utils.data import Dataset, DataLoader
import json

class FeatureMapDataset(Dataset):
    def __init__(self, frames_dir, real_dir, json_file):
        self.frames_dir = frames_dir
        self.real_dir = real_dir

        with open(json_file, 'r') as f:
            self.mappings = json.load(f)

        self.frame_files = list(self.mappings.keys())  # List of frame filenames

    def __len__(self):
        return len(self.frame_files)

    def __getitem__(self, idx):
        frame_file = self.frame_files[idx]
        real_images = self.mappings[frame_file]

        # Load frame feature map
        frame_feature = torch.load(os.path.join(self.frames_dir, frame_file))

        # Load top real world image feature maps
        real_features = [torch.load(os.path.join(self.real_dir, img[0])) for img in real_images]

        # Extract the top real image and its similarity score
        top_real_feature = real_features[0]
        top_similarity = real_images[0][1]

        return frame_feature, top_real_feature, top_similarity, real_features[1:]

# Define data loaders
frames_dir = '/kaggle/working/frames_features/'
real_dir = '/kaggle/working/real_features/'
json_file = '/kaggle/working/*.json'  # or gtav_mapillary.json

dataset = FeatureMapDataset(frames_dir, real_dir, json_file)
dataloader = DataLoader(dataset, batch_size=4, shuffle=True, num_workers=4)

In [151]:
import torch
torch.cuda.empty_cache()

In [ ]:
import os
import torchvision

def setup_distributed():
    dist.init_process_group(backend='nccl')
    torch.cuda.set_device(args.local_rank)

def contrastive_loss(anchor, positive, negatives, margin=0.2):
    # Cosine similarity between anchor and positive (
    pos_sim = F.cosine_similarity(anchor, positive, dim=-1)

    # Cosine similarity between anchor and all negative examples
    neg_sims = [F.cosine_similarity(anchor, neg, dim=-1) for neg in negatives]

    # Calculate loss
    loss = 0.0
    for neg_sim in neg_sims:
        loss += torch.clamp(margin + neg_sim - pos_sim, min=0.0)  # Margin-based contrastive loss

    return loss.mean()

# Training script
import torch
import torch.nn as nn
import torch.nn.functional as F

class MultiClassNPairLoss(nn.Module):
    def __init__(self, temperature=0.07):
        super().__init__()
        self.temperature = temperature

    def forward(self, anchor, positives, negatives):
        # Normalize embeddings
        anchor = F.normalize(anchor, dim=-1)
        positives = F.normalize(positives, dim=-1)
        negatives = F.normalize(negatives, dim=-1)

        # Compute similarities
        pos_sim = torch.sum(anchor * positives, dim=-1) / self.temperature
        neg_sims = torch.sum(anchor.unsqueeze(1) * negatives, dim=-1) / self.temperature

        # Compute loss
        logits = torch.cat([pos_sim.unsqueeze(1), neg_sims], dim=1)
        labels = torch.zeros(logits.shape[0], dtype=torch.long, device=logits.device)
        return F.cross_entropy(logits, labels)

def train_contrastive(model, dataloader, feature_extractor, optimizer, num_epochs=10, alpha=1.0, beta=0.5):
    device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
    model = nn.DataParallel(model).to(device)
    feature_extractor = feature_extractor.to(device)
    contrastive_loss_fn = MultiClassNPairLoss()

    for epoch in range(num_epochs):
        model.train()
        running_loss = 0.0

        for batch_idx, (synthetic_frame, real_images, similarity_scores) in enumerate(dataloader):
            synthetic_frame = synthetic_frame.to(device)
            real_images = [img.to(device) for img in real_images]
            similarity_scores = similarity_scores.to(device)

            optimizer.zero_grad()

            # Forward pass
            reconstructed_frame = model(synthetic_frame)

            # Extract features from real images
            real_features = [feature_extractor(img) for img in real_images]

            # Identify positive and negative pairs
            positive_idx = torch.argmax(similarity_scores, dim=1)
            positive_features = torch.stack([real_features[i][idx] for i, idx in enumerate(positive_idx)])
            negative_features = torch.stack([feat for i, feat in enumerate(real_features) if i != positive_idx])

            # Compute losses
            reconstruction_loss = F.mse_loss(reconstructed_frame, synthetic_frame)
            contrastive_loss = contrastive_loss(reconstructed_frame, positive_features, negative_features)

            # Combine losses
            total_loss = alpha * reconstruction_loss + beta * contrastive_loss

            # Backpropagation and optimization
            total_loss.backward()
            optimizer.step()

            running_loss += total_loss.item()

            if batch_idx % 10 == 0:
                print(f"Epoch [{epoch+1}/{num_epochs}], Batch [{batch_idx}/{len(dataloader)}], "
                      f"Loss: {total_loss.item():.4f}, Recon Loss: {reconstruction_loss.item():.4f}, "
                      f"Contrastive Loss: {contrastive_loss.item():.4f}")

        epoch_loss = running_loss / len(dataloader)
        print(f"Epoch [{epoch+1}/{num_epochs}], Avg Loss: {epoch_loss:.4f}")

    torch.save(model.state_dict(), 'realformer_contrastivev4.pth')

model = RealFormerAGA(img_size=256, patch_size=1, emb_dim=768, num_heads=32, num_layers=16, hidden_dim=3072)
feature_extractor = torchvision.models.resnet50(pretrained=True).features
optimizer = torch.optim.Adam(model.parameters(), lr=0.001)

train_contrastive(model, dataloader, feature_extractor, optimizer, num_epochs=50, alpha=1.0, beta=0.5)

In [ ]:
import os
from huggingface_hub import login, HfApi

# Login to Hugging Face Hub
login(token="")

# Initialize the Hugging Face API
api = HfApi()

# Specify the directory containing the models
model_directory = "/kaggle/working/"
repo_id = "aoxo/RealFormer"
repo_type = "model"

# Loop through all files in the model directory
for filename in os.listdir(model_directory):
    # Only upload files that end with .pth
    if filename.endswith(".pth"):
        file_path = os.path.join(model_directory, filename)
        path_in_repo = filename  # Use the same filename in the repo
        
        # Upload the model file to the repository
        api.upload_file(
            path_or_fileobj=file_path,
            path_in_repo=path_in_repo,
            repo_id=repo_id,
            repo_type=repo_type,
        )
        print(f"Uploaded {filename} to {repo_id} repository.")

In [3]:
total_params = sum(p.numel() for p in model.parameters())
print(total_params)
print(model)
# torch.save(model.state_dict(), 'realformerv4.pth')
# Convert model to FP16 and save
model.half()
torch.save(model.state_dict(), 'realformerv4_fp16.pth')
# Convert model to BF16 and save
model.to(torch.bfloat16)
torch.save(model.state_dict(), 'realformerv4_bf16.pth')
import torch.quantization as quantization

# Apply static quantization to the model
model_int8 = quantization.quantize_dynamic(
    model, {torch.nn.Linear}, dtype=torch.qint8
)

# Save the INT8 quantized model
torch.save(model_int8.state_dict(), 'realformerv4_int8.pth')

651863061
RealFormerAGA(
  (patch_embed): DynamicPatchEmbedding(
    (proj): Conv2d(3, 768, kernel_size=(1, 1), stride=(1, 1))
  )
  (encoder_layers): ModuleList(
    (0-15): 16 x TransformerEncoderBlock(
      (attn): CrossAttentionLayer(
        (attn): MultiheadAttention(
          (out_proj): NonDynamicallyQuantizableLinear(in_features=768, out_features=768, bias=True)
        )
        (dropout): Dropout(p=0.1, inplace=False)
      )
      (ff): Sequential(
        (0): Linear(in_features=768, out_features=3072, bias=True)
        (1): ReLU()
        (2): Linear(in_features=3072, out_features=768, bias=True)
      )
      (norm1): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
      (norm2): StyleAdaptiveLayerNorm(
        (norm): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
        (fc): Linear(in_features=768, out_features=1536, bias=True)
      )
      (dropout): Dropout(p=0.1, inplace=False)
    )
  )
  (decoder_layers): ModuleList(
    (0-15): 16 x Transformer